In [11]:
from Bio import SeqIO #parse fasta files
import os #change directories
import time #track processing time
import pandas as pd #create dataframes
from datasets import load_dataset #load dataframe into huggingface dataset
from sklearn import preprocessing #encode labels
from sklearn.model_selection import train_test_split

import json

In [27]:
#appends the suborf Dicts to a list for easier iteration
#====
fileParse = "parsed_pullin_dict.json"
subOrfList = []
subOrfCounter = 0
#====

with open(f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/{fileParse}", "r+") as json_file:
    #====
    loaded_file = json.load(json_file)
    #====
    
    for listIndex in range(len(loaded_file)):
        #====
        fileDict = loaded_file[listIndex]
        fileKey = list(fileDict.keys())
        fileNameKey = fileKey[0] #key for fileDict
        
        #====
        
        for orfKey in fileDict[fileNameKey]:
            
            if orfKey != "hash":
                #====
                orfDict = fileDict[fileNameKey]
                suborfDict = orfDict[orfKey]
                #====
                for subOrfKey in suborfDict:
                    #print(subOrfCounter, subOrfKey)
                    subOrfCounter += 1
                    #====
                    lowLevelDict = suborfDict[subOrfKey]
                    
                    #====
                    subOrfList.append(lowLevelDict)
                    #print(lowLevelDict)
            
print(len(subOrfList))

2328229


In [61]:
#parses through subOrfList to append info to lists, which will be put into a dict
#====
dict2csv = {}
labelList = []
startList = []
stopList = []
sequenceList = []
#====

for suborfDict in subOrfList:
    labelList.append(suborfDict["full_name"])
    startList.append(suborfDict["start"]) 
    stopList.append(suborfDict["stop"])
    sequenceList.append(suborfDict["sequence"])

# append a "not domain" label to encode
labelList.append("AA_not_domain")
startList.append(1)
stopList.append(6)
sequenceList.append("MGKVALG")
labelList.append("AA_not_domain")
startList.append(1)
stopList.append(5)
sequenceList.append("MGKVAL")
    

print(f"labelList: {len(labelList)}")
print(f"startList: {len(startList)}")
print(f"stopList: {len(stopList)}")
print(f"sequenceList: {len(sequenceList)}")

dict2csv["labels"] = labelList
dict2csv["start"] = startList
dict2csv["stop"] = stopList
dict2csv["sequence"] = sequenceList
print("")
print("========")
print("")
print(dict2csv.keys())
print("")
print(dict2csv["labels"][0])
print(dict2csv["start"][0])
print(dict2csv["stop"][0])
print(dict2csv["sequence"][0])

labelList: 2328231
startList: 2328231
stopList: 2328231
sequenceList: 2328231


dict_keys(['labels', 'start', 'stop', 'sequence'])

AMR_77
448
780
MKSLCYHFIGIGGIGMSALAHILLDRGYSVSGSDLSEGKIVETLKNKGVKFFLGNQEEHVPEESVVVYGSGISKNNPEFLAALNKGNRLIHRAELLAELTKEQISIFVTGSHGKTTVSSLITVILQEAGKTPSFAIGGLNGEGINGSSGSEYFVAEADESDGSIRNYSPEFSVITNIDDEHLSNFGGDRERLLASLQDFSTKTRQICWYNGDCSRLRSCLVGHTFGFTSSCDLHILTYRQEGWRSFFTVRYQNVLYEDVEVRLVGEHNVMNAAAAMGVALSLGIDEDTIRDALQRFPGVQRRLQRKNSSEVFLFLEDYAHHPSEIACTLQAVRSAVGSRRVLAICQPHRFSRLKECMGCFPSAFKGADEVLLTDVYSAGEAEEDVSYKELAQSISRESLVTCAYVPFSELQGFLEKHIRVHDVCVALGAGDIEVLGESLRDFEPKKLSLGLICGGRSCEHDISILSAQNIAKYLSHSFYEVQYFLITREGLWKTGSSLELSEETGKTIFDPEIAGKLSKVDVILPILHGPYGEDGAMQGFLETIGKPYTGPSLVFAAIGMNKVLTKRFMSDLGIPVVPYLPLTLKGWKQDQEKCLAQIKAAFSFPMFVKSVHLGSSIGVFEVHDTNELRDAINEAFVRDDDVFIEESRLGCREIEVSFLGDGSGVFFVAGMHERRGRGGFIDYQEKYGLSGRASAQIVFDVDLSKETREQLLGVAEKIYRLLQGKGSCRIDFFVDNEGSFWLSEINPIPGMTTASPFLAAFVRKGWNREQIVHQLVIDGLQRFDQRQRLISTPLIDQALAAR


In [88]:
p = "FIGIGGIGMSALAHILLDRGYSVSGSDLSEGKIVETLKNKGVKFFLGNQEEHVPEESVVVYGSGISKNNPEFLAALNKGNRLIHRAELLAELTKEQISIFVTGSHGKTTVSSLITVILQEAGKTPSFAIGGLNGEGINGSSGSEYFVAEADESDGSIRNYSPEFSVITNIDDEHLSNFGGDRE"
p = " ".join(p)
p = p.split()
print("".join(p))

FIGIGGIGMSALAHILLDRGYSVSGSDLSEGKIVETLKNKGVKFFLGNQEEHVPEESVVVYGSGISKNNPEFLAALNKGNRLIHRAELLAELTKEQISIFVTGSHGKTTVSSLITVILQEAGKTPSFAIGGLNGEGINGSSGSEYFVAEADESDGSIRNYSPEFSVITNIDDEHLSNFGGDRE


In [62]:
#insert whitespace into sequence and shorten to 512 or maintain lower len
counter = 0
for i in range(len(dict2csv["sequence"])):
    if len(dict2csv["sequence"][i]) > 512:
        newSeq = dict2csv["sequence"][i][:512]
        dict2csv["sequence"][i] = newSeq
        counter += 1
print(counter)
counter = 0
for i in range(len(dict2csv["sequence"])):
    newSeq1 = " ".join(dict2csv["sequence"][i])
    dict2csv["sequence"][i] = newSeq1
    counter += 1
print(counter)

859159
2328231


In [30]:
#shows the frequency of each label
frequencyDict = {}
for i in labelList:
    if i not in frequencyDict:
        frequencyDict[i] = 1
    else:
        frequencyDict[i] += 1

counter = 0
for i in frequencyDict:
    print(i, frequencyDict[i])
    counter += 1
print(counter)

AMR_77 611
KETOSYNTHASE 287148
ADENYLATION 119032
DEHYDRATASE 30627
ACYLTRANSFERASE 127994
THIOLATION 237832
APE_AT 3244
ACYL_ADENYLATING 120760
CONDENSATION 234737
PPTASE 73897
PabC 43388
ECTOINE_SYNTHASE 13190
QueE 541
QueC 536
IMMUNITY_7 2395
BACTERIOCIN_4 4211
BACTERIOCIN_1 1667
IMMUNITY_4 973
IMMUNITY_2 1631
LasI 23610
AMR_211 17611
PhzAB 2217
PhzD 39838
PhzE 1439
PhzF 1199
PhzG 1228
CypA 3983
IsnA 5732
IsnB 5720
PvcC 3620
AMR_246 5196
THIOESTERASE 83977
PxaB 3075
GLYCOSYLTRANSFERASE 26478
AMR_243 491
AMR_244 507
BACTERIOCIN_14 43
AMINOTRANSFERASE 20526
NISc 34892
AMR_286 2934
BACTERIOCIN_52 151
KETOREDUCTASE 13604
Asparagine_synthase 8038
Transglutaminase 7395
Lasso_precursors 6313
AMR_287 159
NITROREDUCTASE 40478
KasQ 971
BACTERIOCIN_26 21025
BACTERIOCIN_80 8527
MtaR 3575
LanKC 8593
Putative_lantipeptide 13977
AMR_201 14549
AMR_262 9791
LanA_4B 4501
LanM 9933
NISb 17659
CHLORINATION 7391
FORMYLTRANSFERASE 6295
BACTERIOCIN_13 1040
PepM 5670
DhpF 5306
BACTERIOCIN_59 1403
AMR_224 2

In [151]:
#convert dict to csv, save as csv
csvName = "parsed_pullin_sequences>100_withAA_not_domain_uneven.csv"

df = pd.DataFrame.from_dict(dict2csv)
df.to_csv(f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/{csvName}")

In [32]:
#reload from csv, drop index column
csvName = "parsed_pullin_sequences>100_withAA_not_domain_uneven.csv"

df = pd.read_csv(f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/{csvName}")

print(df.columns)
df = df.drop(["Unnamed: 0"], axis=1)
print(df.columns)

Index(['Unnamed: 0', 'labels', 'start', 'stop', 'sequence'], dtype='object')
Index(['labels', 'start', 'stop', 'sequence'], dtype='object')


#====

In [76]:
# drops the rows with labels in dropList (removes labels with too few sequences)
print(len(df))
df.set_index("labels", inplace=True)
df.drop(dropList, axis=0, inplace=True)
df.reset_index(inplace=True)
print(len(df))

2328231
2272670


In [77]:
#dropped duplicate rows
print(len(df))
df.drop_duplicates(subset=["sequence", "labels", "start", "stop"], inplace=True) #if we removed "start" we would have 618024 sequences instead, one sequence is exactly the same with just a different start site
print(len(df))

2272670
567934


In [78]:
df.reset_index(inplace=True)
df = df.drop(["index"], axis=1)
df.tail()

labels  start  stop  \
567929  Head_to_tail_precursor      2    63   
567930                   DUF95     12    98   
567931                   DUF95      1    79   
567932           AA_not_domain      1     6   
567933           AA_not_domain      1     5   

                                                 sequence  
567929  M L T M I A D V A A A T G I S T A N A T I V V ...  
567930  M R M D G F T I M K L L N N R K V L L T I T V ...  
567931  M G V Q I S I H H S M S K I L G T L M M H G I ...  
567932                                      M G K V A L G  
567933                                        M G K V A L

In [79]:
#shows the frequency of each label after removing duplicates
frequencyDictAfter = {}

for index, row in df.iterrows():
    if row["labels"] not in frequencyDictAfter:
        frequencyDictAfter[row["labels"]] = 1
    else:
        frequencyDictAfter[row["labels"]] += 1

counter = 0
for i in frequencyDictAfter:
    print(i, frequencyDictAfter[i])
    counter += 1
print(counter)

AMR_77 243
KETOSYNTHASE 71373
ADENYLATION 44017
DEHYDRATASE 10292
ACYLTRANSFERASE 32321
THIOLATION 54516
APE_AT 1248
ACYL_ADENYLATING 21022
CONDENSATION 76506
PPTASE 12767
PabC 5904
ECTOINE_SYNTHASE 3834
QueE 265
QueC 265
IMMUNITY_7 149
BACTERIOCIN_4 881
BACTERIOCIN_1 317
LasI 5777
AMR_211 2898
PhzAB 388
PhzD 3269
PhzE 430
PhzF 245
PhzG 292
CypA 556
IsnA 705
IsnB 758
PvcC 241
AMR_246 1012
THIOESTERASE 22915
PxaB 266
GLYCOSYLTRANSFERASE 4615
AMR_243 110
AMR_244 86
BACTERIOCIN_14 33
AMINOTRANSFERASE 3643
NISc 8134
AMR_286 916
KETOREDUCTASE 7391
Asparagine_synthase 4465
Transglutaminase 3582
Lasso_precursors 1867
AMR_287 105
NITROREDUCTASE 5009
KasQ 619
BACTERIOCIN_26 729
BACTERIOCIN_80 99
LanKC 2745
Putative_lantipeptide 4810
AMR_201 2697
AMR_262 2331
LanA_4B 548
LanM 4022
NISb 2486
CHLORINATION 2777
FORMYLTRANSFERASE 2242
PepM 1970
DhpF 2127
BACTERIOCIN_59 339
AMR_224 986
AgrB 1169
AgrD 504
NISa 2379
AMR_57 15
AMR_32 5
AMR_31 3
AMR_229 10
BACTERIOCIN_109 5
BACTERIOCIN_32 2
AMR_194 188
A

In [80]:
#list out labels with less than 100 samples and remove
dropList = [] #list of labels to drop as they contain less than 100 samples
numToDrop = []
amount  = 0
for i in frequencyDictAfter:
    if frequencyDictAfter[i] < 1000:
        #print(i, frequencyDict[i])
        dropList.append(i)
        numToDrop.append(frequencyDictAfter[i])
        amount += 1
print(len(dropList))
dropList.remove("AA_not_domain")
print(len(dropList))
print("=====")
print(len(numToDrop))
numToDrop.pop(len(numToDrop) - 1)
print(len(numToDrop))

1212
1211
=====
1212
1211


In [81]:
# drops the rows with labels in dropList (removes labels with too few sequences)
print(len(df))
df.set_index("labels", inplace=True)
df.drop(dropList, axis=0, inplace=True)
df.reset_index(inplace=True)
print(len(df))

567934
482099


In [82]:
#shows the frequency of each label after removing sequences with less than 100 samples
frequencyDictAfter = {}

for index, row in df.iterrows():
    if row["labels"] not in frequencyDictAfter:
        frequencyDictAfter[row["labels"]] = 1
    else:
        frequencyDictAfter[row["labels"]] += 1

counter = 0
for i in frequencyDictAfter:
    print(i, frequencyDictAfter[i])
    counter += 1
print(counter)

KETOSYNTHASE 71373
ADENYLATION 44017
DEHYDRATASE 10292
ACYLTRANSFERASE 32321
THIOLATION 54516
APE_AT 1248
ACYL_ADENYLATING 21022
CONDENSATION 76506
PPTASE 12767
PabC 5904
ECTOINE_SYNTHASE 3834
LasI 5777
AMR_211 2898
PhzD 3269
AMR_246 1012
THIOESTERASE 22915
GLYCOSYLTRANSFERASE 4615
AMINOTRANSFERASE 3643
NISc 8134
KETOREDUCTASE 7391
Asparagine_synthase 4465
Transglutaminase 3582
Lasso_precursors 1867
NITROREDUCTASE 5009
LanKC 2745
Putative_lantipeptide 4810
AMR_201 2697
AMR_262 2331
LanM 4022
NISb 2486
CHLORINATION 2777
FORMYLTRANSFERASE 2242
PepM 1970
DhpF 2127
AgrB 1169
NISa 2379
AMR_261 3181
LazC 1058
LazA 1207
BACTERIOCIN_16 1559
ST_1 1256
AMIDOTRANSFERASE 1486
AMR_116 2628
Putative_phosphoramidate 1730
ACYL_COA_DEHYDROGENASE 1204
Putative_lasso_peptide 2491
SbnA 1013
IPM 1325
C_METHYLTRANSFERASE 1684
CDPS 1105
CAPREOMYCIDINE_SYNTHASE_1 1116
MelC2 1311
ENOYLREDUCTASE 4505
LanC 2247
LanB 2678
ABM 1557
AfsA 1983
KSA 1757
CLF 1884
AA_not_domain 2
60


#====

In [83]:
#encode labels and print a list of them with corresponding number label (goes alphabetically)

le = preprocessing.LabelEncoder()
le.fit(df["labels"])

t = list(le.classes_)
n = 0
for i in t:
    print(f"{n}) {i}")
    n += 1

0) AA_not_domain
1) ABM
2) ACYLTRANSFERASE
3) ACYL_ADENYLATING
4) ACYL_COA_DEHYDROGENASE
5) ADENYLATION
6) AMIDOTRANSFERASE
7) AMINOTRANSFERASE
8) AMR_116
9) AMR_201
10) AMR_211
11) AMR_246
12) AMR_261
13) AMR_262
14) APE_AT
15) AfsA
16) AgrB
17) Asparagine_synthase
18) BACTERIOCIN_16
19) CAPREOMYCIDINE_SYNTHASE_1
20) CDPS
21) CHLORINATION
22) CLF
23) CONDENSATION
24) C_METHYLTRANSFERASE
25) DEHYDRATASE
26) DhpF
27) ECTOINE_SYNTHASE
28) ENOYLREDUCTASE
29) FORMYLTRANSFERASE
30) GLYCOSYLTRANSFERASE
31) IPM
32) KETOREDUCTASE
33) KETOSYNTHASE
34) KSA
35) LanB
36) LanC
37) LanKC
38) LanM
39) LasI
40) Lasso_precursors
41) LazA
42) LazC
43) MelC2
44) NISa
45) NISb
46) NISc
47) NITROREDUCTASE
48) PPTASE
49) PabC
50) PepM
51) PhzD
52) Putative_lantipeptide
53) Putative_lasso_peptide
54) Putative_phosphoramidate
55) ST_1
56) SbnA
57) THIOESTERASE
58) THIOLATION
59) Transglutaminase


In [84]:
#add new encoded labels and remove old string labels and save encoded to csv

#====
filename = "encoded_parsed_pullin_noDupes_whiteSpace>1000_withAA_not_domain.csv"
new_labels = le.transform(df["labels"])
new_labels_dict = {"sequence": df["sequence"], "labels": new_labels, "start": df["start"], "stop": df["stop"]}
labelled_df = pd.DataFrame(new_labels_dict)
#====

labelled_df.to_csv(f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/{filename}")


In [7]:
#load encoded csv
filename = "encoded_parsed_pullin_noDupes>1000_withAA_not_domain.csv"

labelled_df = pd.read_csv(f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/{filename}")

print(labelled_df.columns)
labelled_df = labelled_df.drop(["Unnamed: 0"], axis=1)
print(labelled_df.columns)
print(f"length: {len(labelled_df)}")

Index(['Unnamed: 0', 'sequence', 'labels', 'start', 'stop'], dtype='object')
Index(['sequence', 'labels', 'start', 'stop'], dtype='object')
length: 537837


In [90]:
labelled_df.drop(len(labelled_df) - 1, inplace=True)
labelled_df.drop(len(labelled_df) - 1, inplace=True)

train_split, val_split = train_test_split(labelled_df, test_size=.2, random_state=420)#stratify=masterLabel
print(len(train_split))
print(len(val_split))

#parses through each row and creates 2 lists with single amino acid and label
#====
testMasterAcid = []
testMasterLabel = []
#====

for index, row in val_split.iterrows(): #iterates over rows
    #====
    start = row["start"]
    stop = row["stop"]
    sequence = row["sequence"]
    sequence = sequence.split()
    sequence = "".join(sequence)
    print(sequence)
    labels = row["labels"]
    domainList = list(range(start, stop + 1))
    sequenceIndexCounter = 0
    singleAcid = []
    singleLabel = []
    switch = True
    #====
    #print(start, stop)
    #print(domainList[0], domainList[-1])
    
    for currentNum in range(len(sequence)): #iterate over each amino acid in a single sequence
        #====
        currentAcid = sequence[currentNum]
        shiftedNum = currentNum + 1 #index that we compare to as sequence index starts at zero but start/stop starts at 1
        #====
        
        if shiftedNum == domainList[sequenceIndexCounter]:
            if sequenceIndexCounter == 0:
                singleLabel.append(labels)
                singleAcid.append(currentAcid)
                sequenceIndexCounter += 1
            else:
                singleLabel.append(-100)
                singleAcid.append(currentAcid)
#                 print('YES')
                if domainList[sequenceIndexCounter] == domainList[-1]:
                    sequenceIndexCounter = 0
                    switch = True
#                     print("STOPPED SWITCH BACK TRUE SEQUENCE BROKEN")
                else:
                    sequenceIndexCounter += 1
#                     print("Counting")

            
        else:
            if switch == True:
                singleLabel.append(0)
                singleAcid.append(currentAcid)
                switch = False

            else:
                singleLabel.append(-100) #need to add "not domain" label to encoder
                singleAcid.append(currentAcid)

 
            
            
    #print(len(singleAcid))
    #print(len(singleLabel))
    
    testMasterAcid.append(singleAcid)
    testMasterLabel.append(singleLabel)
    
print(len(testMasterAcid))
print(len(testMasterLabel))

print(testMasterAcid[-1])
print(testMasterLabel[-1])
# print(masterAcid.pop(len(masterAcid) - 1))
# print(masterLabel.pop(len(masterLabel) - 1))

print(len(testMasterAcid))
print(len(testMasterLabel))

385676
96419
MRAIILNSGRGSRMGSLTAAQPKCMTEISDSETILSRQLTMLAEAGITDVVITTGAFSGELISYCDNLGLPLDIKFVHNPDFAQTNYIYSIFLAEKLLRGDDVILMHGDLVFERAVFDEVVSCDGSCMAVSLSAQLPEKDFKAVIADGRVKKVGIEFFGKGAAAAQPLYRLTAREWERWLDRICTYCQSGDSEKRRCYAENALNEIVIKDIAPLDTGELLCAEIDTPEDLAAVKEALRKAEERTVYMCFSTDIIHSAHIAMVKRASRLGKLTIGVLSDEAVASYKRYPLLPFEERRTMFANIKGVERAVEQRQLSYRENILKYRPDIVVHGDDWTEGFQKPIRDEVKKLLGSYGGRLVEYPYSNDKKYRELDKRARAELSLPNFRRGRLKKLLGMKKPVTAIEAHSGLTGLIAENTVVYQRGGARQFDAMWISSLCDSTAKGKPDIELVDMTSRYRTIDDIMEVTTKPIIFDGDTGGLTEHFVYTVRTLERMGVSMVIIEDKTGLKKNSLFG
MNKNSNRVQYKDFSVWQNFYDISKQEEYWKREFAGEIARVDLKTDFLRPQIQSFRGDNVVAKVKEPLSSGVKNLALKHGATEFMVTLSVFILLLAKYSRQKDIIVGTTVSGRVHADTKGMLGMFVNTLVIKGEVSPDETFEHLILAVKEKCLQAYDNQEYQFEDLVEAVEKKRDLSRNPIFDFMFGLKEKKKPTEMQGLLGGKSAFIKRNVSKFDLSVLVECMPEGYEIDFEYCTDLFKQETIEYMARHYVTLLEEAITHPGKKLKDLHMLDLREQEKILVDFNATNVEYSREQTAVSLFENQVEKTAGNIALKFDDNKMTYAELNERANQLARTLRDLGVAPNDLVALVTERSMEMIVGILAIIKAGGAYVPINPEYPDNRIQYMLEDSSPKVVLTYKNKLPGKVEIPVLGLEDENNYANETDNLLHVNRSNDLVYCIYTSGTTGNPKGVLIEHRNVVNMWVTYQETFALSDK

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



#++++++++++++++++++++++++++++++++++++++++++++++++++

In [10]:
#load encoded csv
#split, individually label, and tokenize all put together from code below


labelled_df = pd.read_csv(f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/{filename}")

print(labelled_df.columns)
labelled_df = labelled_df.drop(["Unnamed: 0"], axis=1)
print(labelled_df.columns)
print(f"length: {len(labelled_df)}")

labelled_df.drop(len(labelled_df) - 1, inplace=True)
labelled_df.drop(len(labelled_df) - 1, inplace=True)

train_split, val_split = train_test_split(labelled_df, test_size=.2, random_state=420)#stratify=masterLabel
print(len(train_split))
print(len(val_split))

#parses through each row and creates 2 lists with single amino acid and label
#====
testMasterAcid = []
testMasterLabel = []
#====

for index, row in val_split.iterrows(): #iterates over rows
    #====
    start = row["start"]
    stop = row["stop"]
    sequence = row["sequence"]
    labels = row["labels"]
    domainList = list(range(start, stop + 1))
    sequenceIndexCounter = 0
    singleAcid = []
    singleLabel = []
    switch = True
    #====
    #print(start, stop)
    #print(domainList[0], domainList[-1])
    
    for currentNum in range(len(sequence)): #iterate over each amino acid in a single sequence
        #====
        currentAcid = sequence[currentNum]
        shiftedNum = currentNum + 1 #index that we compare to as sequence index starts at zero but start/stop starts at 1
        #====
        
        if shiftedNum == domainList[sequenceIndexCounter]:
            if sequenceIndexCounter == 0:
                singleLabel.append(labels)
                singleAcid.append(currentAcid)
                sequenceIndexCounter += 1
            else:
                singleLabel.append(-100)
                singleAcid.append(currentAcid)
#                 print('YES')
                if domainList[sequenceIndexCounter] == domainList[-1]:
                    sequenceIndexCounter = 0
                    switch = True
#                     print("STOPPED SWITCH BACK TRUE SEQUENCE BROKEN")
                else:
                    sequenceIndexCounter += 1
#                     print("Counting")

            
        else:
            if switch == True:
                singleLabel.append(0)
                singleAcid.append(currentAcid)
                switch = False

            else:
                singleLabel.append(-100) #need to add "not domain" label to encoder
                singleAcid.append(currentAcid)

 
            
            
    #print(len(singleAcid))
    #print(len(singleLabel))
    
    testMasterAcid.append(singleAcid)
    testMasterLabel.append(singleLabel)
    
print(len(testMasterAcid))
print(len(testMasterLabel))

print(testMasterAcid[-1])
print(testMasterLabel[-1])
# print(masterAcid.pop(len(masterAcid) - 1))
# print(masterLabel.pop(len(masterLabel) - 1))

print(len(testMasterAcid))
print(len(testMasterLabel))

#parses through each row and creates 2 lists with single amino acid and label
#====
trainMasterAcid = []
trainMasterLabel = []
#====

for index, row in train_split.iterrows(): #iterates over rows
    #====
    start = row["start"]
    stop = row["stop"]
    sequence = row["sequence"]
    labels = row["labels"]
    domainList = list(range(start, stop + 1))
    sequenceIndexCounter = 0
    singleAcid = []
    singleLabel = []
    switch = True
    #====
    #print(start, stop)
    #print(domainList[0], domainList[-1])
    
    for currentNum in range(len(sequence)): #iterate over each amino acid in a single sequence
        #====
        currentAcid = sequence[currentNum]
        shiftedNum = currentNum + 1 #index that we compare to as sequence index starts at zero but start/stop starts at 1
        #====
        
        if shiftedNum == domainList[sequenceIndexCounter]:
            if sequenceIndexCounter == 0:
                singleLabel.append(labels)
                singleAcid.append(currentAcid)
                sequenceIndexCounter += 1
            else:
                singleLabel.append(-100)
                singleAcid.append(currentAcid)
                if domainList[sequenceIndexCounter] == domainList[-1]:
                    sequenceIndexCounter = 0
                    switch = True
                else:
                    sequenceIndexCounter += 1

            
        else:
            if switch == True:
                singleLabel.append(0)
                singleAcid.append(currentAcid)
                switch = False

            else:
                singleLabel.append(-100) #need to add "not domain" label to encoder
                singleAcid.append(currentAcid)

            
            
    #print(len(singleAcid))
    #print(len(singleLabel))
    
    trainMasterAcid.append(singleAcid)
    trainMasterLabel.append(singleLabel)
    
print(len(trainMasterAcid))
print(len(trainMasterLabel))


print(trainMasterAcid[-1])
print(trainMasterLabel[-1])
# print(masterAcid.pop(len(masterAcid) - 1))
# print(masterLabel.pop(len(masterLabel) - 1))

print(len(trainMasterAcid))
print(len(trainMasterLabel))


#==============
# #TOKENIZE
#==============
# from transformers import BertModel, BertTokenizer
# import re


# tokenizer = BertTokenizer.from_pretrained("Rostlab/prot_bert", do_lower_case=False)
# encoded_train = tokenizer(trainMasterAcid, is_split_into_words=True, padding=True, max_length=512, truncation=True)
# encoded_val = tokenizer(testMasterAcid, is_split_into_words=True, padding=True, max_length=512, truncation=True)

# #create dataset object
# import torch

# class TokenDataset(torch.utils.data.Dataset):
#     def __init__(self, encodings, labels):
#         self.encodings = encodings
#         self.labels = labels
    
#     def __getitem__(self, idx):
#         item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()} #keys are input_ids, token_type_ids, attention_mask, labels, values are stored as a list of lists
#         item['labels'] = torch.tensor(self.labels[idx])
#         return item
    
#     def __len__(self):
#         return (len(self.labels))

# for i in range(len(testMasterLabel)):
#     if len(testMasterLabel[i]) < 512:
#         while len(testMasterLabel[i]) < 512:
#             testMasterLabel[i].append(-100)
#     elif len(testMasterLabel[i]) > 512:
#         testMasterLabel[i] = testMasterLabel[i][:512]

# for i in range(len(trainMasterLabel)):
#     if len(trainMasterLabel[i]) < 512:
#         while len(trainMasterLabel[i]) < 512:
#             trainMasterLabel[i].append(-100)
#     elif len(trainMasterLabel[i]) > 512:
#         trainMasterLabel[i] = trainMasterLabel[i][:512]
        
        
# train_dataset = TokenDataset(encoded_train, trainMasterLabel)
# val_dataset = TokenDataset(encoded_val, testMasterLabel)
# filename1 = ".pt"
# filename2 = "trial_embedding_pullin_val-100.pt"
# torch.save(train_dataset, f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/{filename1}")
# torch.save(val_dataset, f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/{filename2}")

Index(['Unnamed: 0', 'sequence', 'labels', 'start', 'stop'], dtype='object')
Index(['sequence', 'labels', 'start', 'stop'], dtype='object')
length: 610360
488286
122072
122072
122072
['M', 'A', 'H', 'E', 'A', 'V', 'R', 'T', 'T', 'E', 'R', 'I', 'A', 'P', 'L', 'P', 'P', 'A', 'A', 'L', 'G', 'I', 'W', 'F', 'T', 'E', 'Q', 'F', 'N', 'G', 'P', 'S', 'A', 'V', 'Y', 'H', 'I', 'S', 'F', 'T', 'H', 'R', 'L', 'R', 'G', 'P', 'L', 'D', 'P', 'D', 'L', 'L', 'D', 'R', 'A', 'L', 'T', 'A', 'L', 'V', 'H', 'R', 'H', 'E', 'P', 'L', 'R', 'S', 'R', 'I', 'D', 'L', 'I', 'D', 'E', 'E', 'P', 'R', 'Q', 'R', 'V', 'L', 'T', 'P', 'A', 'P', 'F', 'Y', 'A', 'E', 'R', 'V', 'E', 'A', 'K', 'S', 'T', 'G', 'E', 'L', 'P', 'V', 'E', 'V', 'E', 'R', 'H', 'I', 'A', 'E', 'H', 'R', 'S', 'R', 'P', 'F', 'R', 'L', 'A', 'E', 'G', 'D', 'P', 'F', 'R', 'V', 'L', 'L', 'V', 'R', 'L', 'G', 'P', 'E', 'D', 'H', 'V', 'L', 'S', 'A', 'V', 'L', 'H', 'H', 'I', 'C', 'A', 'D', 'G', 'L', 'S', 'L', 'P', 'V', 'L', 'C', 'A', 'D', 'L', 'A', 'A', 'F', 'Y', '

In [13]:
for i in range(len(testMasterLabel)):
    if len(testMasterLabel[i]) < 512:
        while len(testMasterLabel[i]) < 512:
            testMasterLabel[i].append(-100)
    elif len(testMasterLabel[i]) > 512:
        testMasterLabel[i] = testMasterLabel[i][:512]
        
for i in range(len(trainMasterLabel)):
    if len(trainMasterLabel[i]) < 512:
        while len(trainMasterLabel[i]) < 512:
            trainMasterLabel[i].append(-100)
    elif len(trainMasterLabel[i]) > 512:
        trainMasterLabel[i] = trainMasterLabel[i][:512]

In [14]:
print(len(trainMasterAcid))
print(len(trainMasterLabel))
print(len(testMasterAcid))
print(len(testMasterLabel))

488286
488286
122072
122072


#++++++++++++++++++++++++++++++++++++++

In [ ]:
# delete below if shit #good for now

In [55]:
#stratify split dataframe into training split and validation split
train_split, val_split = train_test_split(labelled_df, stratify=labelled_df["labels"], test_size=.2, random_state=420)#stratify=masterLabel
print(len(train_split))
print(len(val_split))

1845581
461396


In [ ]:
#delete above if shit #good for now

In [56]:
#parses through each row and creates 2 lists with single amino acid and label
#====
testMasterAcid = []
testMasterLabel = []
#====

for index, row in val_split.iterrows(): #iterates over rows
    #====
    start = row["start"]
    stop = row["stop"]
    sequence = row["sequence"]
    labels = row["labels"]
    domainList = list(range(start, stop + 1))
    sequenceIndexCounter = 0
    singleAcid = []
    singleLabel = []
    #====
    #print(start, stop)
    #print(domainList[0], domainList[-1])
    
    for currentNum in range(len(sequence)): #iterate over each amino acid in a single sequence
        #====
        currentAcid = sequence[currentNum]
        shiftedNum = currentNum + 1 #index that we compare to as sequence index starts at zero but start/stop starts at 1
        #====
        
        if shiftedNum == domainList[sequenceIndexCounter]:
            singleLabel.append(labels)
            singleAcid.append(currentAcid)
            if domainList[sequenceIndexCounter] == domainList[-1]:
                sequenceIndexCounter = 0
            else:
                sequenceIndexCounter += 1
            
        else:
            singleLabel.append(0) #need to add "not domain" label to encoder
            singleAcid.append(currentAcid)
            
            
    #print(len(singleAcid))
    #print(len(singleLabel))
    
    testMasterAcid.append(singleAcid)
    testMasterLabel.append(singleLabel)
    
print(len(testMasterAcid))
print(len(testMasterLabel))

print(testMasterAcid[-1])
print(testMasterLabel[-1])
# print(masterAcid.pop(len(masterAcid) - 1))
# print(masterLabel.pop(len(masterLabel) - 1))

print(len(testMasterAcid))
print(len(testMasterLabel))

461396
461396
['M', 'S', 'N', 'A', 'V', 'H', 'N', 'I', 'Y', 'A', 'V', 'N', 'R', 'W', 'R', 'P', 'I', 'A', 'G', 'S', 'P', 'S', 'L', 'A', 'T', 'D', 'E', 'S', 'V', 'L', 'V', 'I', 'I', 'P', 'V', 'T', 'S', 'A', 'A', 'G', 'V', 'S', 'P', 'N', 'R', 'Q', 'R', 'L', 'L', 'S', 'W', 'V', 'G', 'G', 'Q', 'A', 'H', 'C', 'S', 'F', 'T', 'A', 'L', 'D', 'T', 'L', 'E', 'R', 'M', 'T', 'A', 'T', 'L', 'A', 'D', 'Y', 'I', 'P', 'G', 'K', 'I', 'K', 'S', 'I', 'L', 'W', 'I', 'G', 'G', 'S', 'L', 'D', 'V', 'S', 'V', 'H', 'A', 'E', 'D', 'Q', 'G', 'L', 'Q', 'Y', 'G', 'I', 'E', 'E', 'K', 'I', 'F', 'F', 'R', 'F', 'F', 'K', 'A', 'L', 'L', 'E', 'L', 'K', 'A', 'D', 'E', 'V', 'R', 'L', 'S', 'I', 'T', 'V', 'V', 'T', 'K', 'N', 'N', 'F', 'N', 'V', 'N', 'N', 'E', 'G', 'T', 'N', 'T', 'A', 'V', 'N', 'A', 'G', 'L', 'H', 'G', 'L', 'V', 'G', 'A', 'A', 'A', 'K', 'E', 'Y', 'S', 'H', 'W', 'T', 'I', 'S', 'L', 'L', 'D', 'V', 'D', 'D', 'A', 'F', 'V', 'A', 'R', 'A', 'T', 'S', 'N', 'P', 'S', 'L', 'V', 'R', 'S', 'S', 'Q', 'G', 'I', 'E', 'K', 

In [ ]:
#parses through each row and creates 2 lists with single amino acid and label
#====
trainMasterAcid = []
trainMasterLabel = []
#====

for index, row in labelled_df.iterrows(): #iterates over rows
    #====
    start = row["start"]
    stop = row["stop"]
    sequence = row["sequence"]
    labels = row["labels"]
    domainList = list(range(start, stop + 1))
    sequenceIndexCounter = 0
    singleAcid = []
    singleLabel = []
    #====
    #print(start, stop)
    #print(domainList[0], domainList[-1])
    
    for currentNum in range(len(sequence)): #iterate over each amino acid in a single sequence
        #====
        currentAcid = sequence[currentNum]
        shiftedNum = currentNum + 1 #index that we compare to as sequence index starts at zero but start/stop starts at 1
        #====
        
        if shiftedNum == domainList[sequenceIndexCounter]:
            singleLabel.append(labels)
            singleAcid.append(currentAcid)
            if domainList[sequenceIndexCounter] == domainList[-1]:
                sequenceIndexCounter = 0
            else:
                sequenceIndexCounter += 1
            
        else:
            singleLabel.append(0) #need to add "not domain" label to encoder
            singleAcid.append(currentAcid)
            
            
    #print(len(singleAcid))
    #print(len(singleLabel))
    
    trainMasterAcid.append(singleAcid)
    trainMasterLabel.append(singleLabel)
    
print(len(trainMasterAcid))
print(len(trainMasterLabel))

print(trainMasterAcid[-1])
print(trainMasterLabel[-1])
# print(masterAcid.pop(len(masterAcid) - 1))
# print(masterLabel.pop(len(masterLabel) - 1))

print(len(trainMasterAcid))
print(len(trainMasterLabel))

# ====tokenize=====

In [10]:
#tokenize 
from transformers import BertModel, BertTokenizer
import re


tokenizer = BertTokenizer.from_pretrained("Rostlab/prot_bert", do_lower_case=False)
encoded_train = tokenizer(trainMasterAcid, is_split_into_words=True, padding=True, max_length=512, truncation=True)
encoded_val = tokenizer(testMasterAcid, is_split_into_words=True, padding=True, max_length=512, truncation=True)

In [2]:
#create dataset object
import torch

class TokenDataset(torch.utils.data.Dataset):
    def __init__(self, encodings, labels):
        self.encodings = encodings
        self.labels = labels
    
    def __getitem__(self, idx):
        item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()} #keys are input_ids, token_type_ids, attention_mask, labels, values are stored as a list of lists
        item['labels'] = torch.tensor(self.labels[idx])
        return item
    
    def __len__(self):
        return (len(self.labels))
    
train_dataset = TokenDataset(encoded_train, trainMasterLabel)
val_dataset = TokenDataset(encoded_val, testMasterLabel)

In [12]:
filename1 = "trial_embedding_pullin_train.pt"
filename2 = "trial_embedding_pullin_val.pt"
torch.save(train_dataset, f"/mnt/storage/grid/home/eric/hmm2bert/pullin_trial/{filename1}")
torch.save(val_dataset, f"/mnt/storage/grid/home/eric/hmm2bert/pullin_trial/{filename2}")

In [31]:
filename1 = "trial_embedding_pullin_val-100.pt"
ds = torch.load(f"/mnt/storage/grid/home/eric/hmm2bert/pullin_trial/{filename1}")

In [32]:
for row in ds:
    for column in row:
        if column == "labels":
            print(row[column])
            label = row[column]
            for element in range(len(label)):
                if label[element] == 0:
                    label[element] = -100
            print(label)

tensor([-100, -100, -100,  ..., -100, -100, -100])
tensor([-100, -100, -100,  ..., -100, -100, -100])
tensor([-100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100,
        -100, -100, -100, -100,   28,   28,   28,   28,   28,   28,   28,   28,
          28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,
          28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,
          28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,
          28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,
          28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,
          28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,
          28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,
          28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,
          28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,   28,
          28,   28

In [16]:
for row in ds:
    for column in row:
        if column == "labels":
            print(row[column])

tensor([7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7,
        7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 0, 0])
tensor([0, 0, 0,  ..., 0, 0, 0])
tensor([ 0,  0,  0,  0,  0, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35,
        35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35,
        35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35,
        35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35, 35,
        35,  0,  0,  0,  0,  0])
tensor([ 0, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32,
        32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32,
        32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32,
        32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32,
        32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32,
        32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 3

# ====individually label with 0 and -100====

In [3]:
#load encoded csv
#split, individually label, and tokenize all put together from code below


labelled_df = pd.read_csv(f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/{filename}")

print(labelled_df.columns)
labelled_df = labelled_df.drop(["Unnamed: 0"], axis=1)
print(labelled_df.columns)
print(f"length: {len(labelled_df)}")

#drop the two AA_not_domain rows
labelled_df.drop(2306975, inplace=True)
labelled_df.drop(2306976, inplace=True)

print(f"length: {len(labelled_df)}")

train_split, val_split = train_test_split(labelled_df, test_size=.2, random_state=420, stratify=labelled_df["labels"])#stratify=masterLabel
print(len(train_split))
print(len(val_split))

#parses through each row and creates 2 lists with single amino acid and label
#====
testMasterAcid = []
testMasterLabel = []
#====

for index, row in val_split.iterrows(): #iterates over rows
    #====
    start = row["start"]
    stop = row["stop"]
    sequence = row["sequence"]
    labels = row["labels"]
    domainList = list(range(start, stop + 1))
    sequenceIndexCounter = 0
    singleAcid = []
    singleLabel = []
    #====
    #print(start, stop)
    #print(domainList[0], domainList[-1])
    
    for currentNum in range(len(sequence)): #iterate over each amino acid in a single sequence
        #====
        currentAcid = sequence[currentNum]
        shiftedNum = currentNum + 1 #index that we compare to as sequence index starts at zero but start/stop starts at 1
        #====
        
        if shiftedNum == domainList[sequenceIndexCounter]:
            if domainList[0] == domainList[sequenceIndexCounter]:
                singleLabel.append(labels)
                singleAcid.append(currentAcid)
                sequenceIndexCounter += 1
            else:
                singleLabel.append(-100)
                singleAcid.append(currentAcid)
                if domainList[sequenceIndexCounter] == domainList[-1]:
                    sequenceIndexCounter = 0
                else:
                    sequenceIndexCounter += 1
            
        else:
            singleLabel.append(0) #need to add "not domain" label to encoder
            singleAcid.append(currentAcid)
            
            
    #print(len(singleAcid))
    #print(len(singleLabel))
        
    testMasterAcid.append(singleAcid)
    testMasterLabel.append(singleLabel)
    
print(len(testMasterAcid))
print(len(testMasterLabel))

print(testMasterAcid[0])
print(testMasterLabel[0])
# print(masterAcid.pop(len(masterAcid) - 1))
# print(masterLabel.pop(len(masterLabel) - 1))

print(len(testMasterAcid))
print(len(testMasterLabel))

# #parses through each row and creates 2 lists with single amino acid and label
# #====
# trainMasterAcid = []
# trainMasterLabel = []
# #====

# for index, row in train_split.iterrows(): #iterates over rows
#     #====
#     start = row["start"]
#     stop = row["stop"]
#     sequence = row["sequence"]
#     labels = row["labels"]
#     domainList = list(range(start, stop + 1))
#     sequenceIndexCounter = 0
#     singleAcid = []
#     singleLabel = []
#     #====
#     #print(start, stop)
#     #print(domainList[0], domainList[-1])
    
#     for currentNum in range(len(sequence)): #iterate over each amino acid in a single sequence
#         #====
#         currentAcid = sequence[currentNum]
#         shiftedNum = currentNum + 1 #index that we compare to as sequence index starts at zero but start/stop starts at 1
#         #====
        
#         if shiftedNum == domainList[sequenceIndexCounter]:
#             if domainList[0] == domainList[sequenceIndexCounter]:
#                 singleLabel.append(labels)
#                 singleAcid.append(currentAcid)
#                 sequenceIndexCounter += 1
#             else:
#                 singleLabel.append(-100)
#                 singleAcid.append(currentAcid)
#                 if domainList[sequenceIndexCounter] == domainList[-1]:
#                     sequenceIndexCounter = 0
#                 else:
#                     sequenceIndexCounter += 1
            
#         else:
#             singleLabel.append(0) #need to add "not domain" label to encoder
#             singleAcid.append(currentAcid)
            
            
#     #print(len(singleAcid))
#     #print(len(singleLabel))
    
#     trainMasterAcid.append(singleAcid)
#     trainMasterLabel.append(singleLabel)
    
# print(len(trainMasterAcid))
# print(len(trainMasterLabel))

# print(trainMasterAcid[0])
# print(trainMasterLabel[0])
# # print(masterAcid.pop(len(masterAcid) - 1))
# # print(masterLabel.pop(len(masterLabel) - 1))

# print(len(trainMasterAcid))
# print(len(trainMasterLabel))


#==============
# #TOKENIZE
#==============
# from transformers import BertModel, BertTokenizer
# import re


# tokenizer = BertTokenizer.from_pretrained("Rostlab/prot_bert", do_lower_case=False)
# encoded_train = tokenizer(trainMasterAcid, is_split_into_words=True, padding=True, max_length=512, truncation=True)
# encoded_val = tokenizer(testMasterAcid, is_split_into_words=True, padding=True, max_length=512, truncation=True)

# #create dataset object
# import torch

# class TokenDataset(torch.utils.data.Dataset):
#     def __init__(self, encodings, labels):
#         self.encodings = encodings
#         self.labels = labels
    
#     def __getitem__(self, idx):
#         item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()} #keys are input_ids, token_type_ids, attention_mask, labels, values are stored as a list of lists
#         item['labels'] = torch.tensor(self.labels[idx])
#         return item
    
#     def __len__(self):
#         return (len(self.labels))

# for i in range(len(testMasterLabel)):
#     if len(testMasterLabel[i]) < 512:
#         while len(testMasterLabel[i]) < 512:
#             testMasterLabel[i].append(-100)
#     elif len(testMasterLabel[i]) > 512:
#         testMasterLabel[i] = testMasterLabel[i][:512]

# for i in range(len(trainMasterLabel)):
#     if len(trainMasterLabel[i]) < 512:
#         while len(trainMasterLabel[i]) < 512:
#             trainMasterLabel[i].append(-100)
#     elif len(trainMasterLabel[i]) > 512:
#         trainMasterLabel[i] = trainMasterLabel[i][:512]
        
        
# train_dataset = TokenDataset(encoded_train, trainMasterLabel)
# val_dataset = TokenDataset(encoded_val, testMasterLabel)
# filename1 = ".pt"
# filename2 = "trial_embedding_pullin_val-100.pt"
# torch.save(train_dataset, f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/{filename1}")
# torch.save(val_dataset, f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/{filename2}")

Index(['Unnamed: 0', 'sequence', 'labels', 'start', 'stop'], dtype='object')
Index(['sequence', 'labels', 'start', 'stop'], dtype='object')
length: 2306977
length: 2306975
1845580
461395
461395
461395
['M', 'N', 'Q', 'T', 'I', 'L', 'N', 'R', 'V', 'K', 'T', 'R', 'V', 'M', 'H', 'Q', 'L', 'V', 'S', 'S', 'L', 'I', 'Y', 'E', 'N', 'I', 'V', 'V', 'Y', 'K', 'A', 'S', 'Y', 'Q', 'D', 'G', 'V', 'G', 'H', 'F', 'T', 'I', 'E', 'G', 'H', 'D', 'S', 'E', 'Y', 'R', 'F', 'T', 'A', 'E', 'K', 'T', 'H', 'S', 'F', 'D', 'R', 'I', 'R', 'I', 'T', 'S', 'P', 'I', 'E', 'R', 'V', 'V', 'G', 'D', 'E', 'A', 'D', 'T', 'T', 'T', 'D', 'Y', 'T', 'Q', 'L', 'L', 'R', 'E', 'A', 'V', 'F', 'T', 'F', 'P', 'K', 'N', 'D', 'E', 'K', 'L', 'E', 'Q', 'F', 'I', 'V', 'E', 'L', 'L', 'Q', 'T', 'E', 'L', 'K', 'D', 'T', 'Q', 'S', 'M', 'Q', 'Y', 'R', 'E', 'S', 'N', 'P', 'P', 'A', 'T', 'P', 'E', 'T', 'F', 'N', 'D', 'Y', 'E', 'F', 'Y', 'A', 'M', 'E', 'G', 'H', 'Q', 'Y', 'H', 'P', 'S', 'Y', 'K', 'S', 'R', 'L', 'G', 'F', 'T', 'L', 'S', 'D', 'N'

In [4]:
for i in range(len(testMasterLabel)):
    if len(testMasterLabel[i]) < 512:
        while len(testMasterLabel[i]) < 512:
            testMasterLabel[i].append(-100)
    elif len(testMasterLabel[i]) > 512:
        testMasterLabel[i] = testMasterLabel[i][:512]
        
# for i in range(len(trainMasterLabel)):
#     if len(trainMasterLabel[i]) < 512:
#         while len(trainMasterLabel[i]) < 512:
#             trainMasterLabel[i].append(-100)
#     elif len(trainMasterLabel[i]) > 512:
#         trainMasterLabel[i] = trainMasterLabel[i][:512]

In [5]:
#create dataset object
import torch

class TokenDataset(torch.utils.data.Dataset):
    def __init__(self, encodings, labels):
        self.encodings = encodings
        self.labels = labels
    
    def __getitem__(self, idx):
        item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()} #keys are input_ids, token_type_ids, attention_mask, labels, values are stored as a list of lists
        item['labels'] = torch.tensor(self.labels[idx])
        return item
    
    def __len__(self):
        return (len(self.labels))

saved_strat_train = f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/embedding_pullin_train>100_stratified.pt"
saved_strat_val = f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/embedding_pullin_val>100_stratified.pt"

#train_pull = torch.load(saved_strat_train)
val_pull = torch.load(saved_strat_val)

In [6]:
#convert from lists of labels to tensor
for listIndex in range(len(testMasterLabel)):
    testMasterLabel[listIndex] = torch.IntTensor(testMasterLabel[listIndex])

In [7]:
#faster version
#takes loaded bad tensor and extracts tokenized keys to a list (encodingList)
inputList = []
tokenList = []
attentionList = []
for dictL in val_pull:
    inputList.append(dictL["input_ids"])
    tokenList.append(dictL["token_type_ids"])
    attentionList.append(dictL["attention_mask"])

valMasterDict = {"input_ids": inputList, "token_type_ids": tokenList, "attention_mask": attentionList, "labels": testMasterLabel}

In [8]:
print(valMasterDict["input_ids"][0])
print(valMasterDict["token_type_ids"][0])
print(valMasterDict["attention_mask"][0])
print(valMasterDict["labels"][0])

tensor([ 2, 21, 17, 18, 15, 11,  5, 17, 13,  8, 12, 15, 13,  8, 21, 22, 18,  5,
         8, 10, 10,  5, 11, 20,  9, 17, 11,  8,  8, 20, 12,  6, 10, 20, 18, 14,
         7,  8,  7, 22, 19, 15, 11,  9,  7, 22, 14, 10,  9, 20, 13, 19, 15,  6,
         9, 12, 15, 22, 10, 19, 14, 13, 11, 13, 11, 15, 10, 16, 11,  9, 13,  8,
         8,  7, 14,  9,  6, 14, 15, 15, 15, 14, 20, 15, 18,  5,  5, 13,  9,  6,
         8, 19, 15, 19, 16, 12, 17, 14,  9, 12,  5,  9, 18, 19, 11,  8,  9,  5,
         5, 18, 15,  9,  5, 12, 14, 15, 18, 10, 21, 18, 20, 13,  9, 10, 17, 16,
        16,  6, 15, 16,  9, 15, 19, 17, 14, 20,  9, 19, 20,  6, 21,  9,  7, 22,
        18, 20, 22, 16, 10, 20, 12, 10, 13,  5,  7, 19, 15,  5, 10, 14, 17,  5,
        12, 19,  7, 16, 14, 19,  8, 16, 17, 11, 12,  5,  5, 24,  5,  6, 11, 14,
        12,  7, 12,  8,  9, 15, 15,  8, 10, 13, 17,  8,  8,  8, 17,  9, 21,  5,
        13, 18, 18,  8,  7, 14, 12, 15, 20,  9, 22, 19,  8, 18, 18, 11,  9,  6,
        10,  7, 12, 22,  8, 17, 14,  8, 

In [9]:
class newDataset(torch.utils.data.Dataset):
    def __init__(self, dataframe):
        self.encodings = {"input_ids": dataframe["input_ids"], "token_type_ids": dataframe["token_type_ids"], "attention_mask": dataframe["attention_mask"]}
        self.labels = {"labels": dataframe["labels"]}
        
    
    def __getitem__(self, idx):
        item = {"input_ids": self.encodings["input_ids"][idx], "token_type_ids": self.encodings["token_type_ids"][idx], "attention_mask": self.encodings["attention_mask"][idx], "labels": self.labels["labels"][idx]}
        return item
    
    def __len__(self):
        return(len(self.labels["labels"]))

In [10]:
pleaseWork = newDataset(valMasterDict)
torch.save(pleaseWork, f"/mnt/storage/grid/home/eric/hmm2bert/pullin_parsed_data/embedding_pullin_val>100_stratified_withAA_not_domain_notebook_2.pt")

In [28]:
pleaseWork[0]

{'input_ids': tensor([ 2, 21, 17, 18, 15, 11,  5, 17, 13,  8, 12, 15, 13,  8, 21, 22, 18,  5,
          8, 10, 10,  5, 11, 20,  9, 17, 11,  8,  8, 20, 12,  6, 10, 20, 18, 14,
          7,  8,  7, 22, 19, 15, 11,  9,  7, 22, 14, 10,  9, 20, 13, 19, 15,  6,
          9, 12, 15, 22, 10, 19, 14, 13, 11, 13, 11, 15, 10, 16, 11,  9, 13,  8,
          8,  7, 14,  9,  6, 14, 15, 15, 15, 14, 20, 15, 18,  5,  5, 13,  9,  6,
          8, 19, 15, 19, 16, 12, 17, 14,  9, 12,  5,  9, 18, 19, 11,  8,  9,  5,
          5, 18, 15,  9,  5, 12, 14, 15, 18, 10, 21, 18, 20, 13,  9, 10, 17, 16,
         16,  6, 15, 16,  9, 15, 19, 17, 14, 20,  9, 19, 20,  6, 21,  9,  7, 22,
         18, 20, 22, 16, 10, 20, 12, 10, 13,  5,  7, 19, 15,  5, 10, 14, 17,  5,
         12, 19,  7, 16, 14, 19,  8, 16, 17, 11, 12,  5,  5, 24,  5,  6, 11, 14,
         12,  7, 12,  8,  9, 15, 15,  8, 10, 13, 17,  8,  8,  8, 17,  9, 21,  5,
         13, 18, 18,  8,  7, 14, 12, 15, 20,  9, 22, 19,  8, 18, 18, 11,  9,  6,
         10,  7